# EPS 109, Final Project: Bird Flocking Simulation
### Ashley Chu, Wednesday 5-7PM

In [ ]:
import numpy as np
from matplotlib import pyplot as plt
%matplotlib osx

In [ ]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

- Initialize points
- Run passes on the n times for each part of the simulation

- separation
- alignment
- cohesion


In [ ]:
"""
Applies the 3 flocking rules to the particles

https://www.red3d.com/cwr/boids/
"""
def flocking_rules(birds, velocities, max_v, radius, total, xlim, ylim):
    change_in_pos = np.zeros((total,2))
    
    for i in range(total):
        bird = birds[i]
        bird_v = velocities[i]
        
        position_from_bird = birds - bird
        #calculates distance between all birds in birds and bird
        distances = np.linalg.norm(position_from_bird, axis=1)
        
        # Alignment velocity calculation --> finds mean of all birds within radius
        alignment_velocity = np.mean(velocities[distances < radius], axis = 0)
        
        #Cohesion velocity calculation -- calculated using the distances of all the nearby birds within the radius
        avg_pos = np.mean(birds[distances < radius], axis=0)
        cohesion_velocity = (avg_pos-bird)/total
        
        #Separation velocity calculation -- calculated via reversal of cohesion velocity 
        #Need to cap when referencing itself within birds
        non_zero_dist = np.where(distances == 0, 0.00001, distances)[distances < radius, None]
        opposite_pos_from_bird = (bird - birds[distances < radius]) #Computes all birds in radius to bird
        separation_velocity = np.sum(opposite_pos_from_bird / non_zero_dist, axis=0) #sum all individual neighbors and averaged

        change_in_pos[i] = bird_v + alignment_velocity + cohesion_velocity + separation_velocity
        
    #Retrieve scalar value between all x and y velocity components for singular speed for all birds
    speeds = np.linalg.norm(change_in_pos, axis=1) 
    
    #adjust position to be at max speed of 5
    scalar = max_v / speeds[speeds > max_v, None]
    change_in_pos[speeds > max_v] = change_in_pos[speeds > max_v] * scalar
    return change_in_pos

In [ ]:
def step(birds, velocities, max_v, radius, total, xlim, ylim):
    old_birds = birds
    velocities = flocking_rules(birds, velocities, max_v, radius, total, xlim, ylim)
    
    for b in range(total):
        #Bouncing
        if (birds[b][0] >= xlim or birds[b][0] <= 2):
            velocities[b][0] *= -1
        if (birds[b][1] >= ylim or birds[b][1] <= 2):
            velocities[b][1] *= -1
        
        #Entering other side
#         if (birds[b][0] >= xlim):
#             birds[b][0] = 2
#         elif (birds[b][0] <= 2):
#             birds[b][0] = xlim
            
#         if (birds[b][1] >= ylim):
#             birds[b][1] = 2
#         elif birds[b][1] <= 2:
#             birds[b][1] = ylim
            
    birds = birds+ velocities * .5 #.5 is some arbitrary dt
    return old_birds, birds, velocities

In [ ]:
fig = plt.figure()
        
with writer.saving(fig, "animation1.mp4", dpi=200):
    total = 50
    # np.random.seed(0)

    #Initialize parameters
    birds = np.random.uniform(60, 140, size=(total, 2))
    max_v = 5
    velocities = np.random.uniform(low=-max_v, high=max_v, size=(total, 2))
    radius = 10.
    xlim, ylim = 198, 198
    
    #300 steps 300/15 = 20 second animation
    for i in range(300):
        old_birds, birds, velocities = step(birds, velocities, max_v, radius, total, xlim, ylim)
        plt.clf()
        for i in range(len(old_birds)):
            dx = birds[i, 0] - old_birds[i, 0]
            dy = birds[i, 1] - old_birds[i, 1]
            plt.arrow(old_birds[i, 0], old_birds[i, 1], dx, dy, shape='full', lw=0, length_includes_head=True, head_width=3)
        plt.xlim(0, xlim)
        plt.ylim(0, ylim)
        plt.title('ODE Bird Flocking Simulation')
        plt.figtext(0.5, 0.01, 'A bird flocking simulation for EPS 109 by Ashley Chu', wrap=True, horizontalalignment='center', fontsize=12)
        plt.draw()
        plt.pause(0.0001)
        writer.grab_frame()